In [1]:
import json
import os
import pytest
import pycountry
import altair as alt
import plotly.express as px
import numpy as np
import pandas as pd
from countryinfo import CountryInfo
from functools import lru_cache
from rapidfuzz import process
from scipy import stats
from sklearn.preprocessing import MultiLabelBinarizer, LabelBinarizer
from func_library import *



In [2]:
stack_overflow, skills_list, employments = StackOverflowData.generate_aggregate_df(only_data_science_devs=True)
exchange_rate_df = generate_exchange_rates_df()
ppp_df = read_ppp()
stack_overflow = StackOverflowData.generate_2023_usd_comp(stack_overflow, exchange_rate_df, ppp_df)

ai_salaries_df = AISalariesData.generate_df()
ai_salaries_df = AISalariesData.generate_2023_usd_comp(ai_salaries_df, exchange_rate_df, ppp_df)
ai_salaries_df['usd_2023'].describe()

ai_salaries_df = ai_salaries_df.dropna(subset=['usd_2023'])
stack_overflow = stack_overflow.dropna(subset=['usd_2023'])


/Users/aaronrdankert/Desktop/milestone_1/func_library.py:893: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['compensation'] = df.apply(correct_comp, axis=1)


Country code MM not found in pycountry
Country code ME not found in pycountry
Country code AD not found in pycountry
Country code PS not found in pycountry
Country code SY or year 2020 not found in the PPP DataFrame
Country code None or year 2020 not found in the PPP DataFrame
Country code None or year 2020 not found in the PPP DataFrame
Country code None or year 2020 not found in the PPP DataFrame
Country code None or year 2020 not found in the PPP DataFrame
Country code None or year 2020 not found in the PPP DataFrame
Country code None or year 2020 not found in the PPP DataFrame
Country code CU or year 2020 not found in the PPP DataFrame
Country code SY or year 2020 not found in the PPP DataFrame
Country code SY or year 2020 not found in the PPP DataFrame
Country code CU or year 2020 not found in the PPP DataFrame
Country code None or year 2020 not found in the PPP DataFrame
Country code None or year 2020 not found in the PPP DataFrame
Country code CU or year 2020 not found in the PP

/Users/aaronrdankert/Desktop/milestone_1/func_library.py:1168: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[           nan            nan            nan            nan
            nan            nan            nan            nan
            nan            nan            nan            nan
            nan            nan            nan            nan
            nan            nan            nan            nan
            nan            nan            nan            nan
            nan            nan            nan            nan
            nan            nan            nan            nan
            nan            nan            nan            nan
            nan            nan            nan            nan
            nan            nan            nan            nan
            nan            nan            nan            nan
            nan            nan            nan            nan
            nan

Country code GI or year 2023 not found in the PPP DataFrame
Country code AS or year 2022 not found in the PPP DataFrame
Country code AS or year 2021 not found in the PPP DataFrame


In [3]:
ai_q3 = ai_salaries_df['usd_2023'].quantile(0.75)
ai_q1 = ai_salaries_df['usd_2023'].quantile(0.25)
ai_iqr = ai_q3 - ai_q1
ai_lower_bound = ai_q1 - (1.5 * ai_iqr)
ai_upper_bound = ai_q3 + (1.5 * ai_iqr)
filtered_ai_salaries_df = ai_salaries_df[(ai_salaries_df['usd_2023'] > ai_lower_bound) & (ai_salaries_df['usd_2023'] < ai_upper_bound)]


so_q3 = stack_overflow['usd_2023'].quantile(0.75)
so_q1 = stack_overflow['usd_2023'].quantile(0.25)
so_iqr = so_q3 - so_q1
so_lower_bound = so_q1 - (1.5 * so_iqr)
so_upper_bound = so_q3 + (1.5 * so_iqr)
filtered_stack_overflow = stack_overflow[(stack_overflow['usd_2023'] > so_lower_bound) & (stack_overflow['usd_2023'] < so_upper_bound)]
t_stat, p_value = stats.ttest_ind(filtered_ai_salaries_df['usd_2023'], filtered_stack_overflow['usd_2023'], equal_var=True)

print(t_stat, p_value)

91.94994848386212 0.0


In [4]:
from scipy import stats
t_stat, p_value = stats.ttest_ind(filtered_ai_salaries_df['usd_2023'], filtered_stack_overflow['usd_2023'], equal_var=True)
print(f"The t-statistic is {t_stat} and the p-value is {p_value}.")

The t-statistic is 91.94994848386212 and the p-value is 0.0.


In [5]:

# Add a 'Source' column to each dataframe
filtered_ai_salaries_df['source'] = 'AI-jobs.net'
filtered_stack_overflow['source'] = 'StackOverflow'
filtered_ai_salaries_df['country'] = filtered_ai_salaries_df['company_location']

# change all work_year values to strings; rename to 'year'
filtered_ai_salaries_df['work_year'] = filtered_ai_salaries_df['work_year'].astype(str)
filtered_ai_salaries_df['year'] = filtered_ai_salaries_df['work_year']
combined_df = pd.concat([filtered_ai_salaries_df[['usd_2023', 'source', 'country', 'year']], filtered_stack_overflow[['usd_2023', 'source', 'country', 'year']]])


# Ensure Altair can handle the data size if necessary
alt.data_transformers.disable_max_rows()
print(combined_df.sample(20))

combined_df['year'].value_counts()

            usd_2023         source country  year
9579   144200.000000    AI-jobs.net      US  2022
11371   18187.535844  StackOverflow      ID  2020
8694    84115.980000    AI-jobs.net      US  2022
3731    59574.077474  StackOverflow      IN  2020
43893   95200.000000  StackOverflow      US  2019
22894  121000.000000  StackOverflow      US  2021
34438   10780.072565  StackOverflow      KZ  2022
10027   27945.658160  StackOverflow      IN  2020
5367   267720.000000    AI-jobs.net      US  2023
15023  121404.682274  StackOverflow      IL  2021
14624  159500.000000  StackOverflow      US  2021
27942  201302.931596  StackOverflow      CA  2022
19765   41363.102233  StackOverflow      BR  2021
14387   42570.836213  StackOverflow      SE  2021
40050   67850.877193  StackOverflow      CH  2019
43318  101150.000000  StackOverflow      US  2019
25315   92050.209205  StackOverflow      CA  2023
165     49789.029536  StackOverflow      CA  2020
3314   100000.000000    AI-jobs.net      US  2023


/var/folders/gw/9t1pgdqs0p172hmjwq0rgc2c0000gn/T/ipykernel_42428/3146278748.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_ai_salaries_df['source'] = 'AI-jobs.net'
/var/folders/gw/9t1pgdqs0p172hmjwq0rgc2c0000gn/T/ipykernel_42428/3146278748.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_stack_overflow['source'] = 'StackOverflow'
/var/folders/gw/9t1pgdqs0p172hmjwq0rgc2c0000gn/T/ipykernel_42428/3146278748.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slic

year
2019    15436
2020    10372
2023    10266
2021     8887
2022     8033
Name: count, dtype: int64

In [7]:
df_2019 = combined_df[combined_df['year'] == '2019'] 
df_2023 = combined_df[combined_df['year'] == '2023']

# Only keep countries with 10+ observations
country_counts_2019 = df_2019.country.value_counts()
country_counts_2023 = df_2023.country.value_counts()
valid_countries = country_counts_2019[country_counts_2019 >= 10].index.intersection(
                    country_counts_2023[country_counts_2023 >= 10].index)

df_2019 = df_2019[df_2019['country'].isin(valid_countries)]
df_2023 = df_2023[df_2023['country'].isin(valid_countries)]

# Calculate averages for each country and year
df_2019 = df_2019.groupby('country')['usd_2023'].mean().reset_index()
df_2023 = df_2023.groupby('country')['usd_2023'].mean().reset_index()

# Merge and calculate deltas
change_19_23_df = df_2019.merge(df_2023, on='country')
change_19_23_df['delta'] = change_19_23_df['usd_2023_y'] - change_19_23_df['usd_2023_x']
change_19_23_df['pct_change'] = change_19_23_df['delta'] / change_19_23_df['usd_2023_x'] * 100
change_19_23_df = change_19_23_df[['country', 'usd_2023_x', 'usd_2023_y', 'delta', 'pct_change']]
change_19_23_df.columns = ['country', '2019_comp', '2023_comp', 'delt', 'percent_change']


In [8]:
def layered_distribution_chart(combined_df):
    
    background_color = COLOR_THEME['background']

    bar_colors = {
        'AI-jobs.net': COLOR_THEME['secondary'],
        'StackOverflow': COLOR_THEME['primary']
    }

    chart = alt.Chart(combined_df.sort_values(by=['source'], ascending=False)).mark_bar(opacity=1,
                                                                                        binSpacing=0.3,
                                                                                        cornerRadiusTopLeft=4,
                                                                                        cornerRadiusTopRight=4).encode(
        alt.X('usd_2023:Q', bin=alt.Bin(maxbins=50), title='USD 2023 Salary'),
        alt.Y('count()', stack=None, title='Count'),
        alt.Color('source:N', legend=alt.Legend(title="Dataset", orient='top-right', 
                                                fillColor=background_color, labelColor=COLOR_THEME['text'], 
                                                titleColor=COLOR_THEME['text'], titlePadding=5, 
                                                labelLimit=200, padding=5), 
                scale=alt.Scale(domain=list(bar_colors.keys()), range=list(bar_colors.values()))),
    ).properties(
        width=600,
        height=400,
        title="Salary Distribution Comparison",
        background=background_color
    ).configure_view(
        stroke=background_color,
        fill=background_color
    ).configure_axis(
        labelColor=COLOR_THEME['text'],
        titleColor=COLOR_THEME['text']
    )
    return chart

dist_chart = layered_distribution_chart(combined_df)
dist_chart.display()



alt.Chart(...)

In [48]:
def generate_country_chart(country, combined_df, width=300, height=200, max_bins=50):
    background_color = COLOR_THEME['background']
    stat_color = COLOR_THEME['bold']
    country_df = combined_df[combined_df['country'] == country]
    country_name = pycountry.countries.get(alpha_2=country).name
    mean_value = country_df['usd_2023'].mean()
    std_dev = country_df['usd_2023'].std()
    # Define the color scheme for each source
    bar_colors = {
        'AI-jobs.net': COLOR_THEME['secondary'],
        'StackOverflow': COLOR_THEME['primary']
    }
    mean_label_df = pd.DataFrame({'mean': [mean_value], 'label': [f'mean: {abbreviate_salary(mean_value)}']})
    std_dev_label_df = pd.DataFrame({'std_deviations': [mean_value + std_dev, mean_value - std_dev],
                                    'label': [f'+std: {abbreviate_salary(mean_value + std_dev)}', f'-std: {abbreviate_salary(mean_value - std_dev)}']})

    # Create a horizontal bar chart with stacked sources
    chart = alt.Chart(country_df).mark_bar(cornerRadiusTopRight=3).encode(
        x=alt.X('count():O', title=''),
        y=alt.Y('usd_2023:Q', bin=alt.Bin(maxbins=max_bins), title=''),
        color=alt.Color('source:N', scale=alt.Scale(domain=list(bar_colors.keys()), range=list(bar_colors.values())), legend=None)
    )

    upper_std_line = alt.Chart(std_dev_label_df).mark_rule(color=stat_color, strokeWidth=1.5).encode(
        y='std_deviations:Q'
    )

    upper_std_text = alt.Chart(std_dev_label_df).mark_text(
        align='right', dx=5, dy=-5, color=COLOR_THEME['text'], fontSize=10, baseline='middle'
    ).encode(
        y='std_deviations:Q',
        x=alt.value(width),
        text='label:N'
    )

    lower_std_line = alt.Chart(std_dev_label_df).mark_rule(color=stat_color, strokeWidth=1.5, strokeDash =[100,100]).encode(
        y='std_deviations:Q'
    )

    lower_std_text = alt.Chart(std_dev_label_df).mark_text(
        align='right', dx=5, dy=-5, color=COLOR_THEME['text'], fontSize=10, baseline='middle'
    ).encode(
        y='std_deviations:Q',
        x=alt.value(width),
        text='label:N'
    )


    mean_line = alt.Chart(pd.DataFrame({'mean': [mean_value]})).mark_rule(color=stat_color, strokeWidth=3).encode(
        y='mean:Q'
    )

    mean_text = alt.Chart(mean_label_df).mark_text(
        align='right', dx=5, dy=-5, color=COLOR_THEME['text'], fontSize=10, baseline='middle'
    ).encode(
        y=alt.Y('mean:Q', axis=alt.Axis(title='')),
        x=alt.value(width),
        text='label:N'
    )

    final_chart = alt.layer(chart, mean_line, mean_text, upper_std_line, upper_std_text, lower_std_line, lower_std_text).properties(
        width=width,
        height=height,
        title=alt.TitleParams(country_name, color=COLOR_THEME['text'], fontSize=14, anchor='start'),
    )
    return final_chart

def stacked_country_distributions(combined_df, country_count=10, width=300, height=200, min_observations =50):

    country_counts = combined_df['country'].value_counts().sort_values(ascending=False)
    filtered_countries = country_counts[country_counts > min_observations].index.tolist()

    country_charts = []
    for country in filtered_countries[:country_count]:
        country_chart = generate_country_chart(country=country, combined_df=combined_df, width=width, height=height)
        country_charts.append(country_chart)

    stacked_charts = alt.vconcat(*country_charts).properties(
        background=COLOR_THEME['background']
        ).configure_view(
            stroke=COLOR_THEME['background'],
            fill=COLOR_THEME['background'],
        ).configure_axis(
            grid=False,
            ticks=False,
            domain=False,
            labels=False
        ).configure_axisX(
            titlePadding=10,
            labelPadding=5,
            labels=True
        )

    return stacked_charts

#stacked_charts = stacked_country_distributions(combined_df, country_count=75, width=300, height=200, min_observations=50)
#stacked_charts.display()

In [ ]:
#from vega_datasets import data

combined_df['country_alpha_3'] = combined_df['country'].apply(lambda x: convert_country_alpha2_to_alpha3(x))

# Now, calculate the average salary by country using the alpha-3 codes
country_salaries = combined_df.groupby('country_alpha_3')['usd_2023'].mean().reset_index()
country_salaries.columns = ['id', 'average_salary']  # Rename columns for joining with GeoJSON
country_salaries = country_salaries.dropna(subset=['average_salary', 'id'])



# Create the choropleth map with Plotly Express
fig = px.choropleth(country_salaries,
                    locations='id',
                    color='average_salary',
                    hover_name='id',
                    color_continuous_scale=[COLOR_THEME['secondary'], COLOR_THEME['light_accent']])

fig.update_geos(
    landcolor=COLOR_THEME['alt_background'],  # Neutral color for land
    lakecolor=COLOR_THEME['alt_blue'],  # Color for lakes
    showocean=True,
    showcountries=True
)

fig.update_layout(
    paper_bgcolor=COLOR_THEME['background'],
    plot_bgcolor=COLOR_THEME['background'],
    title_font_color=COLOR_THEME['text'],
    font_color=COLOR_THEME['text'],
    geo=dict(
        bgcolor=COLOR_THEME['background'],
        showframe=False,
        showcoastlines=False,
        projection_scale=1,  # Adjust as needed
        center=dict(lat=30, lon=0),  # Adjust as needed
    ),
    margin=dict(l=0, r=0, t=50, b=0)  # Minimize margins around the map
)

fig.update_coloraxes(colorbar=dict(
    title='Average Salary',
    titleside='right',
    titlefont=dict(size=12, color=COLOR_THEME['text']),
    tickfont=dict(color=COLOR_THEME['text']),
    bgcolor=COLOR_THEME['background']
))

# Display the figure
#fig.show()


In [53]:
combined_df

country      2019_comp      2023_comp          delt  percent_change
0       AU   86164.744324   93107.526740   6942.782416        8.057567
1       BR   48364.144122   60033.624037  11669.479915       24.128371
2       CA   87114.317381  102068.053509  14953.736129       17.165647
3       CH   94170.151479  122149.493243  27979.341764       29.711476
4       CN   59980.736050  105539.861731  45559.125681       75.956263
5       CO   53716.219553  110787.213992  57070.994439      106.245367
6       CZ   76971.284689   78393.817204   1422.532515        1.848134
7       DE   87621.919631  114156.648114  26534.728483       30.283208
8       DK   96163.556556  104498.484848   8334.928293        8.667450
9       ES   64276.882841   77355.191689  13078.308848       20.346831
10      FR   69848.943688   95554.997489  25706.053801       36.802352
11      GB   89725.884106   96817.293011   7091.408905        7.903415
12      HU   63310.964314  102547.725255  39236.760941       61.974670
13      IL  103100.897124  135397.199252  32296.302129       31.324948
14      IN   55465.363436   88824.578251  33359.214814       60.144228
15      JP   78613.980612   75363.806245  -3250.174368       -4.134347
16      MX   44651.167046   63056.294780  18405.127734       41.219813
17      MY   54841.565781   97232.440007  42390.874226       77.296980
18      NO   80648.106752   63894.823132 -16753.283620      -20.773313
19      NZ   76505.439335   96106.577524  19601.138189       25.620581
20      PH   45645.934974   80841.769125  35195.834152       77.106174
21      PL   93037.649582  113301.728878  20264.079297       21.780515
22      PT   50134.741681   75109.890110  24975.148429       49.816051
23      RO  114140.101778  131679.764244  17539.662466       15.366784
24      RU   76818.699559   48828.908741 -27989.790818      -36.436169
25      SE   71281.104504   71453.983450    172.878946        0.242531
26      TR   65642.051411   80860.179465  15218.128053       23.183505
27      TW   61783.714919   72512.998267  10729.283348       17.365876
28      UA   90804.176072  100870.796649  10066.620577       11.086077
29      US  123849.912209  154588.687179  30738.774970       24.819376
30      VN   45514.494265   26280.501851 -19233.992415      -42.259049
31      ZA   98564.482338  100608.447489   2043.965151        2.073734

In [43]:
#from vega_datasets import data
change_19_23_df['country_alpha_3'] = change_19_23_df['country'].apply(lambda x: convert_country_alpha2_to_alpha3(x))

# Create the choropleth map with Plotly Express
fig = px.choropleth(change_19_23_df,
                    locations='country_alpha_3',
                    color='percent_change',
                    hover_name='country_alpha_3',
                    color_continuous_scale=[COLOR_THEME['bold'], 'lightgrey', COLOR_THEME['secondary']],
                    color_continuous_midpoint=0)

fig.update_geos(
    landcolor=COLOR_THEME['alt_background'],  # Neutral color for land
    lakecolor=COLOR_THEME['primary'],  # Color for lakes
    oceancolor=COLOR_THEME['primary'],  # Color for ocean
    showocean=True,
    showcountries=True # Show country borders
)

fig.update_layout(
    paper_bgcolor=COLOR_THEME['alt_background'],
    plot_bgcolor=COLOR_THEME['alt_background'],
    title_font_color=COLOR_THEME['text'],
    font_color=COLOR_THEME['text'],
    geo=dict(
        bgcolor=COLOR_THEME['alt_background'],
        showframe=False,
        showcoastlines=False,
        projection_scale=1.1,
        center=dict(lat=30, lon=0), # change the center of the map
    ),
    margin=dict(l=0, r=0, t=0, b=0)  # Minimize margins around the map
)

fig.update_coloraxes(colorbar=dict(
    title=r'Net % change in average salary 2019-2023',
    titleside='right',
    titlefont=dict(size=12, color=COLOR_THEME['text']),
    tickfont=dict(color=COLOR_THEME['text']),
    bgcolor=COLOR_THEME['alt_background'],
    len= 0.8,
    y=.42
))

# Display the figure
fig.show()
